In [1]:
%load_ext rpy2.ipython

In [2]:
%%R
set.seed(88888888) # maximum luck

library(DESeq2)
library(plotly)
library(ggplot2)
library(viridis)
library(magrittr)
library(pheatmap)
library(DescTools)
library(pdfCluster)
library(RColorBrewer)
library(SummarizedExperiment)
library(caret)
library(class)
library(htmlwidgets)

Loading required package: S4Vectors
Loading required package: stats4
Loading required package: BiocGenerics

Attaching package: ‘BiocGenerics’

The following objects are masked from ‘package:stats’:

    IQR, mad, sd, var, xtabs

The following objects are masked from ‘package:base’:

    anyDuplicated, aperm, append, as.data.frame, basename, cbind,
    colnames, dirname, do.call, duplicated, eval, evalq, Filter, Find,
    get, grep, grepl, intersect, is.unsorted, lapply, Map, mapply,
    match, mget, order, paste, pmax, pmax.int, pmin, pmin.int,
    Position, rank, rbind, Reduce, rownames, sapply, setdiff, sort,
    table, tapply, union, unique, unsplit, which.max, which.min


Attaching package: ‘S4Vectors’

The following object is masked from ‘package:utils’:

    findMatches

The following objects are masked from ‘package:base’:

    expand.grid, I, unname

Loading required package: IRanges
Loading required package: GenomicRanges
Loading required package: GenomeInfoDb
Loading require

In [3]:
%%R
OUT_DIR <- "/mnt/home/yuankeji/RanceLab/reticula_new/reticula/data/tcdd/output/"
N_FOLDS <- 10

In [4]:
%%R
vst.counts <- readRDS(paste(OUT_DIR, "vst_counts1vs0_time_cross.Rds", sep = ""))
print(vst.counts)

class: DESeqTransform 
dim: 9297 94 
metadata(1): version
assays(1): ''
rownames(9297): ENSMUSG00000000001 ENSMUSG00000000028 ...
  ENSMUSG00000118462 ENSMUSG00000118541
rowData names(4): baseMean baseVar allZero dispFit
colnames(94): SRR7817611 SRR7817612 ... SRR4317639 SRR4317640
colData names(3): Sample Dose sizeFactor


In [5]:
%%R
sample <- colData(vst.counts)
# print(sample)

In [6]:
%%R
vst.count.mtx <-
   vst.counts %>% SummarizedExperiment::assay() %>% as.data.frame()
print(length(vst.count.mtx))
 head(vst.count.mtx)

[1] 94
                   SRR7817611 SRR7817612 SRR7817614 SRR7817615 SRR7817616
ENSMUSG00000000001  15.366226  15.385352  15.323282  15.407190  15.373202
ENSMUSG00000000028   9.071365   8.930182   9.174159   9.022666   9.089843
ENSMUSG00000000049  19.760640  19.739387  19.987250  19.956171  19.955941
ENSMUSG00000000058   9.660207   9.797899   9.833148   9.548686  10.079037
ENSMUSG00000000085  11.476251  11.212976  11.378731  11.377008  10.995916
ENSMUSG00000000088  16.471526  16.475140  16.445582  16.127523  16.073318
                   SRR7817623 SRR7817624 SRR7817625 SRR7817626 SRR7817627
ENSMUSG00000000001  15.292278  15.321152  15.509121  15.469873  15.285885
ENSMUSG00000000028   9.245988   9.061614   8.964968   9.122937   9.643817
ENSMUSG00000000049  19.970869  19.943545  19.902624  19.901515  19.925020
ENSMUSG00000000058   9.816114  10.183031   9.598356   9.760343   9.720866
ENSMUSG00000000085  11.171083  11.453491  11.578955  11.399844  11.072408
ENSMUSG00000000088  16.023825  

ENSMUSG00000000085  10.888213  10.898497  11.098325  11.115325  10.958062
ENSMUSG00000000088  14.815235  14.683798  15.298009  15.283428  15.497311
                   SRR3593558 SRR3593559 SRR4317608 SRR4317637 SRR4317638
ENSMUSG00000000001  14.900934  14.773152  14.555504  15.167266  15.131304
ENSMUSG00000000028   9.280395   9.382237   9.670392   8.961689   8.442572
ENSMUSG00000000049  19.733540  19.860067  20.106131  20.125750  20.116733
ENSMUSG00000000058   9.915923  10.060304   9.869435  10.651108  10.554802
ENSMUSG00000000085  10.960296  11.219025  11.429956  11.201153  11.223716
ENSMUSG00000000088  15.453992  15.288479  14.763692  15.046956  15.088134
                   SRR4317641 SRR4317642 SRR4317607 SRR4317609 SRR4317610
ENSMUSG00000000001   15.44942  15.358078   14.67507  14.960988  15.084018
ENSMUSG00000000028    9.26334   8.893471    9.23128   9.506458   9.323571
ENSMUSG00000000049   19.92082  19.934405   20.11059  20.177173  20.188574
ENSMUSG00000000058   10.58335  10.5946

In [7]:
%%R
tcdd_dose_detail.vec <-
   readRDS(paste(OUT_DIR, "tcdd_dose_detail_vec1vs0_time_cross.Rds", sep = ""))
print(tcdd_dose_detail.vec)

 [1] 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
[39] 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 0 0 0 1 1 1 1 0 0 0 0 0 1 1
[77] 1 1 1 1 1 1 0 1 1 1 1 0 0 0 0 0 1 1


In [8]:
%%R
rxn2ensembls.nls <-
   readRDS(paste(OUT_DIR, "rxn2ensembls_nls1vs0_time_cross.Rds", sep = ""))
print(length(rxn2ensembls.nls))
print(rxn2ensembls.nls)

[1] 9825
$`R-MMU-170666`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSMUSG00000057614"

$`R-MMU-170671`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSMUSG00000057614"

$`R-MMU-170674`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSM

 [46] "ENSMUSG00000028777" "ENSMUSG00000028950" "ENSMUSG00000028971"
 [49] "ENSMUSG00000029064" "ENSMUSG00000029072" "ENSMUSG00000029236"
 [52] "ENSMUSG00000029371" "ENSMUSG00000029372" "ENSMUSG00000029373"
 [55] "ENSMUSG00000029379" "ENSMUSG00000029380" "ENSMUSG00000029417"
 [58] "ENSMUSG00000029530" "ENSMUSG00000029663" "ENSMUSG00000029713"
 [61] "ENSMUSG00000029819" "ENSMUSG00000031778" "ENSMUSG00000031861"
 [64] "ENSMUSG00000031980" "ENSMUSG00000032192" "ENSMUSG00000032562"
 [67] "ENSMUSG00000032766" "ENSMUSG00000033717" "ENSMUSG00000034117"
 [70] "ENSMUSG00000034855" "ENSMUSG00000035042" "ENSMUSG00000035383"
 [73] "ENSMUSG00000035431" "ENSMUSG00000035448" "ENSMUSG00000036353"
 [76] "ENSMUSG00000036362" "ENSMUSG00000036381" "ENSMUSG00000036402"
 [79] "ENSMUSG00000036437" "ENSMUSG00000036832" "ENSMUSG00000037010"
 [82] "ENSMUSG00000037014" "ENSMUSG00000037140" "ENSMUSG00000037346"
 [85] "ENSMUSG00000037944" "ENSMUSG00000038607" "ENSMUSG00000038668"
 [88] "ENSMUSG00000038811" "ENSMUS

 [4] "ENSMUSG00000019775" "ENSMUSG00000020599" "ENSMUSG00000021219"
 [7] "ENSMUSG00000024186" "ENSMUSG00000026357" "ENSMUSG00000026358"
[10] "ENSMUSG00000026475" "ENSMUSG00000026527" "ENSMUSG00000026678"
[13] "ENSMUSG00000028777" "ENSMUSG00000029101" "ENSMUSG00000032562"
[16] "ENSMUSG00000038530" "ENSMUSG00000042671" "ENSMUSG00000051079"
[19] "ENSMUSG00000052087" "ENSMUSG00000057614" "ENSMUSG00000059810"

$`R-MMU-8982019`
 [1] "ENSMUSG00000000001" "ENSMUSG00000002458" "ENSMUSG00000002459"
 [4] "ENSMUSG00000019775" "ENSMUSG00000020599" "ENSMUSG00000021219"
 [7] "ENSMUSG00000024186" "ENSMUSG00000026357" "ENSMUSG00000026358"
[10] "ENSMUSG00000026475" "ENSMUSG00000026527" "ENSMUSG00000026678"
[13] "ENSMUSG00000028777" "ENSMUSG00000029101" "ENSMUSG00000032562"
[16] "ENSMUSG00000038530" "ENSMUSG00000042671" "ENSMUSG00000051079"
[19] "ENSMUSG00000052087" "ENSMUSG00000057614" "ENSMUSG00000059810"

$`R-MMU-8982020`
 [1] "ENSMUSG00000000001" "ENSMUSG00000002458" "ENSMUSG00000002459"
 [4] "ENSMUS

 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000024325" "ENSMUSG00000025577" "ENSMUSG00000025578"
 [7] "ENSMUSG00000026021" "ENSMUSG00000026484" "ENSMUSG00000026739"
[10] "ENSMUSG00000028796" "ENSMUSG00000037652" "ENSMUSG00000039989"
[13] "ENSMUSG00000040669"

$`R-MMU-4570463`
 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000020265" "ENSMUSG00000020738" "ENSMUSG00000024325"
 [7] "ENSMUSG00000025577" "ENSMUSG00000025578" "ENSMUSG00000026484"
[10] "ENSMUSG00000026739" "ENSMUSG00000028796" "ENSMUSG00000031347"
[13] "ENSMUSG00000037652" "ENSMUSG00000039989" "ENSMUSG00000040669"

$`R-MMU-4570499`
 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000020738" "ENSMUSG00000021546" "ENSMUSG00000024325"
 [7] "ENSMUSG00000025577" "ENSMUSG00000025578" "ENSMUSG00000026484"
[10] "ENSMUSG00000026739" "ENSMUSG00000028796" "ENSMUSG00000037652"
[13] "ENSMUSG00000039989" "ENSMUSG00000040669"

$`R-MM

 [1] "ENSMUSG00000000126" "ENSMUSG00000009900" "ENSMUSG00000010797"
 [4] "ENSMUSG00000012282" "ENSMUSG00000015957" "ENSMUSG00000018486"
 [7] "ENSMUSG00000021994" "ENSMUSG00000022382" "ENSMUSG00000022996"
[10] "ENSMUSG00000022997" "ENSMUSG00000026167" "ENSMUSG00000027840"
[13] "ENSMUSG00000028173" "ENSMUSG00000029671" "ENSMUSG00000030093"
[16] "ENSMUSG00000030170" "ENSMUSG00000033227" "ENSMUSG00000036856"
[19] "ENSMUSG00000036961"

$`R-MMU-3781943`
 [1] "ENSMUSG00000000126" "ENSMUSG00000009900" "ENSMUSG00000010797"
 [4] "ENSMUSG00000012282" "ENSMUSG00000015957" "ENSMUSG00000018486"
 [7] "ENSMUSG00000021994" "ENSMUSG00000022382" "ENSMUSG00000022996"
[10] "ENSMUSG00000022997" "ENSMUSG00000026167" "ENSMUSG00000027840"
[13] "ENSMUSG00000028173" "ENSMUSG00000029671" "ENSMUSG00000030093"
[16] "ENSMUSG00000030170" "ENSMUSG00000033227" "ENSMUSG00000036856"
[19] "ENSMUSG00000036961"

$`R-MMU-205328`
[1] "ENSMUSG00000000127" "ENSMUSG00000005672" "ENSMUSG00000019966"
[4] "ENSMUSG00000032113" "ENSM

...

[1] "ENSMUSG00000039153"

$`R-NUL-9009236`
[1] "ENSMUSG00000039153"

$`R-NUL-844613`
[1] "ENSMUSG00000039193"

$`R-MMU-2454264`
[1] "ENSMUSG00000039194"

$`R-MMU-2465971`
[1] "ENSMUSG00000039194"

$`R-MMU-8960973`
[1] "ENSMUSG00000039194"

$`R-MMU-109624`
[1] "ENSMUSG00000039197"

$`R-MMU-9754974`
[1] "ENSMUSG00000039197"

$`R-MMU-8848392`
[1] "ENSMUSG00000039217" "ENSMUSG00000070427"

$`R-MMU-8931648`
[1] "ENSMUSG00000039242" "ENSMUSG00000039952"

$`R-MMU-6788855`
[1] "ENSMUSG00000039253"

$`R-MMU-9603984`
[1] "ENSMUSG00000039357" "ENSMUSG00000046152" "ENSMUSG00000049307"
[4] "ENSMUSG00000055373"

$`R-MMU-9629360`
[1] "ENSMUSG00000039396"

$`R-MMU-9629363`
[1] "ENSMUSG00000039396"

$`R-MMU-9629370`
[1] "ENSMUSG00000039396"

$`R-MMU-9629470`
[1] "ENSMUSG00000039396"

$`R-MMU-9629485`
[1] "ENSMUSG00000039396"

$`R-MMU-9629492`
[1] "ENSMUSG00000039396"

$`R-MMU-9629509`
[1] "ENSMUSG00000039396"

$`R-MMU-9629510`
[1] "ENSMUSG00000039396"

$`R-MMU-5634802`
 [1] "ENSMUSG00000039410" "ENSMUS

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)




$`R-MMU-2855259`
[1] "ENSMUSG00000046402"

$`R-MMU-74843`
[1] "ENSMUSG00000046402"

$`R-MMU-9717444`
[1] "ENSMUSG00000046480" "ENSMUSG00000057182" "ENSMUSG00000070304"

$`R-MMU-5625717`
[1] "ENSMUSG00000046532" "ENSMUSG00000057672"

$`R-MMU-5625738`
[1] "ENSMUSG00000046532" "ENSMUSG00000057672"

$`R-MMU-73912`
[1] "ENSMUSG00000046598"

$`R-MMU-73920`
[1] "ENSMUSG00000046598"

$`R-MMU-1640164`
[1] "ENSMUSG00000046697"

$`R-MMU-9766551`
[1] "ENSMUSG00000046714" "ENSMUSG00000048387" "ENSMUSG00000050295"

$`R-MMU-442422`
[1] "ENSMUSG00000046822" "ENSMUSG00000052310" "ENSMUSG00000063354"
[4] "ENSMUSG00000072572"

$`R-MMU-8874364`
[1] "ENSMUSG00000046873"

$`R-MMU-8936519`
[1] "ENSMUSG00000046949"

$`R-MMU-1482745`
[1] "ENSMUSG00000046971" "ENSMUSG00000070719" "ENSMUSG00000098488"

$`R-MMU-1482771`
[1] "ENSMUSG00000046971" "ENSMUSG00000050211" "ENSMUSG00000056220"
[4] "ENSMUSG00000060675" "ENSMUSG00000070719" "ENSMUSG00000098488"

$`R-MMU-1482828`
[1] "ENSMUSG00000046971" "ENSMUSG0000005021

[1] "ENSMUSG00000052593" "ENSMUSG00000055737"

$`R-NUL-1251988`
[1] "ENSMUSG00000052593"

$`R-NUL-2484957`
[1] "ENSMUSG00000052593"

$`R-MMU-77608`
[1] "ENSMUSG00000052595"

$`R-MMU-71775`
[1] "ENSMUSG00000052738" "ENSMUSG00000061838"

$`R-MMU-9684627`
[1] "ENSMUSG00000052821"

$`R-MMU-9690439`
[1] "ENSMUSG00000052821"

$`R-MMU-114553`
[1] "ENSMUSG00000052889" "ENSMUSG00000078816"

$`R-MMU-1168373`
[1] "ENSMUSG00000052889"

$`R-MMU-5223304`
[1] "ENSMUSG00000052889"

$`R-MMU-4551446`
[1] "ENSMUSG00000052920"

$`R-MMU-6807585`
[1] "ENSMUSG00000052922"

$`R-MMU-390912`
[1] "ENSMUSG00000053004"

$`R-MMU-9692539`
[1] "ENSMUSG00000053004"

$`R-MMU-202709`
[1] "ENSMUSG00000053062"

$`R-MMU-1254248`
[1] "ENSMUSG00000053110" "ENSMUSG00000062209"

$`R-MMU-1254251`
[1] "ENSMUSG00000053110" "ENSMUSG00000062209"

$`R-MMU-2032770`
[1] "ENSMUSG00000053110"

$`R-MMU-2032775`
[1] "ENSMUSG00000053110" "ENSMUSG00000055320"

$`R-MMU-163320`
[1] "ENSMUSG00000053178"

$`R-MMU-8851988`
[1] "ENSMUSG0000005321

[1] "ENSMUSG00000057963"

$`R-MMU-1855172`
[1] "ENSMUSG00000057963"

$`R-MMU-1855197`
[1] "ENSMUSG00000057963"

$`R-MMU-1855219`
[1] "ENSMUSG00000057963"

$`R-MMU-2267372`
[1] "ENSMUSG00000057963"

$`R-MMU-994137`
[1] "ENSMUSG00000057963"

$`R-MMU-994140`
[1] "ENSMUSG00000057963"

$`R-MMU-2467775`
[1] "ENSMUSG00000058290"

$`R-MMU-5223305`
[1] "ENSMUSG00000058355" "ENSMUSG00000066800"

$`R-MMU-8985201`
[1] "ENSMUSG00000058355" "ENSMUSG00000066800"

$`R-MMU-196402`
[1] "ENSMUSG00000058454"

$`R-MMU-6807055`
[1] "ENSMUSG00000058454"

$`R-MMU-9816403`
[1] "ENSMUSG00000058550" "ENSMUSG00000059552" "ENSMUSG00000072419"

$`R-MMU-9816449`
[1] "ENSMUSG00000058550" "ENSMUSG00000059552" "ENSMUSG00000072419"

$`R-MMU-8849857`
[1] "ENSMUSG00000058579"

$`R-MMU-1461971`
[1] "ENSMUSG00000058618" "ENSMUSG00000060208" "ENSMUSG00000061958"
[4] "ENSMUSG00000064213" "ENSMUSG00000074437" "ENSMUSG00000074442"
[7] "ENSMUSG00000074447" "ENSMUSG00000079120" "ENSMUSG00000094818"

$`R-MMU-1461982`
[1] "ENSMUSG0

In [9]:
%%R
rxns <- rxn2ensembls.nls %>% names()

In [10]:
%%R
rxn_knn_misclass_rate.nls <- list()
rxn_knn_ari.nls <- list()
rxn_knn_ecount.nls <- list()
rxn_pca.nls <- list()
count <- 0

In [11]:
%%R
toi_indices <- seq(1,length(tcdd_dose_detail.vec))
print(toi_indices)

In [12]:
%%R
tcdd_dose_detail_vec_tis_of_interest <-
   tcdd_dose_detail.vec[toi_indices]
print(tcdd_dose_detail_vec_tis_of_interest)

In [13]:
%%R
vst.count.mtx.tis_of_interest <- vst.count.mtx[, toi_indices]
print(vst.count.mtx.tis_of_interest)


ENSMUSG00000016087   9.260981   9.562064   9.483784   9.511174   9.545382
ENSMUSG00000016128  13.975228  14.135628  14.095308  14.131068  14.111427
ENSMUSG00000016181  11.136464  10.915450  11.254330  11.289541  11.295226
ENSMUSG00000016194  18.579149  18.572148  18.503722  18.469400  18.418845
ENSMUSG00000016206  10.051008   9.803985   9.675451  10.252887  10.154915
ENSMUSG00000016252  15.164448  15.162325  15.524755  15.599051  15.720430
ENSMUSG00000016253  13.093178  12.967020  13.094618  13.421236  13.504234
ENSMUSG00000016255   8.750335   8.247333   8.284164   8.278929   7.705505
ENSMUSG00000016256  16.723878  16.685039  16.584743  16.633165  16.608082
ENSMUSG00000016283   8.432194   7.695631   7.707481   7.705801   7.705505
ENSMUSG00000016308  12.869282  12.840883  12.561548  12.882886  12.782863
ENSMUSG00000016319  17.544535  17.570509  17.409808  17.470368  17.700275
ENSMUSG00000016327   7.696316   7.695631   7.707481   7.705801   7.705505
ENSMUSG00000016356   9.858297   9.735

ENSMUSG00000001750  14.306541  13.942834  13.962025  13.966188  13.874567
ENSMUSG00000001751  12.903662  12.955698  13.071563  13.028339  13.278244
ENSMUSG00000001755  16.067360  16.159791  16.196229  16.211166  16.269477
ENSMUSG00000001761  10.721399  10.472922  10.652922  10.763920  10.763874
ENSMUSG00000001767  11.811433  11.815288  11.656890  11.632802  11.708066
ENSMUSG00000001768  11.910443  11.652697  12.045411  11.744172  11.828778
ENSMUSG00000001773   7.705505   7.720943   7.720532   7.692155   7.692525
ENSMUSG00000001786  12.456921  12.713129  12.718254  12.873325  12.726861
ENSMUSG00000001794  15.587360  15.243403  15.145319  15.480547  15.533158
ENSMUSG00000001804   7.705505   7.720943   7.720532   7.692155   7.692525
ENSMUSG00000001827   7.705505   7.720943   7.720532   7.692155   7.692525
ENSMUSG00000001833  13.656918  13.559649  13.759329  13.694867  13.718694
ENSMUSG00000001847  15.470188  15.562689  15.682242  15.667844  15.692660
ENSMUSG00000001855  11.891775  11.5652

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



   8.542188   8.237720
ENSMUSG00000004565  14.236817  13.435122  13.066261  13.519935  13.563918
ENSMUSG00000004567  13.879999  14.026202  14.136562  14.206130  14.272681
ENSMUSG00000004568  13.494999  12.718920  12.560318  13.066961  12.808729
ENSMUSG00000004591  13.734216  13.647131  13.798262  13.852888  13.942083
ENSMUSG00000004609   8.950171   9.412632   9.300709   9.495975   9.095275
ENSMUSG00000004610  17.118652  16.775021  16.703002  16.830799  16.823110
ENSMUSG00000004626  13.910705  13.763154  13.959534  13.912666  13.946508
ENSMUSG00000004630   9.025349   8.813787   8.549000   8.594891   8.479851
ENSMUSG00000004633  12.766554  13.756085  13.786634  13.862748  13.762740
ENSMUSG00000004637  11.162047  11.273177  11.598689  11.407244  11.780495
ENSMUSG00000004642  11.559317  11.543996  11.735605  11.644700  11.723698
ENSMUSG00000004651   7.705505   7.720943   7.720532   7.692155   7.692525
ENSMUSG00000004654   7.705505   7.720943   7.720532   7.692155   7.692525
ENSMUSG00000004

ENSMUSG00000005615  15.036165  15.357474  15.086715  15.157289  15.073556
ENSMUSG00000005625  15.960123  15.564657  15.436249  15.745520  15.705345
ENSMUSG00000005628   9.136617   8.665679   8.287054   8.729965   8.682159
ENSMUSG00000005667   9.674429   8.785087   8.668870   9.137795   9.283779
ENSMUSG00000005672  10.586263  10.654991  10.470511  10.402641  10.394360
ENSMUSG00000005677  16.856458  17.198565  17.172239  17.061328  17.038626
ENSMUSG00000005681  21.524718  21.106121  21.103592  21.149705  21.162113
ENSMUSG00000005682  14.105979  14.278273  14.073886  14.283528  14.308015
ENSMUSG00000005683  16.110557  15.914650  15.997899  16.220945  16.215020
ENSMUSG00000005686   9.092101   9.827220   9.430900   8.866024   9.230241
ENSMUSG00000005687  13.186623  12.955376  13.124564  13.329776  13.321600
ENSMUSG00000005698  13.243005  13.176879  13.265671  13.267094  13.277764
ENSMUSG00000005699  10.068129   9.731312   9.645894   9.458867   9.562993
ENSMUSG00000005705   8.819294   8.3263

...

ENSMUSG00000003411   7.735140   8.596003   7.709728   8.764728   8.470536
ENSMUSG00000003418   9.050821   8.663800   7.709728   7.674489   7.676749
ENSMUSG00000003421  12.476749  12.649732  12.441593  12.436239  12.414201
ENSMUSG00000003429  15.522701  15.470683  15.208648  15.435539  15.459743
ENSMUSG00000003435  14.530389  14.620301  14.495108  14.148200  14.270445
ENSMUSG00000003436   7.735140   7.666953   7.709728   7.674489   7.676749
ENSMUSG00000003437  13.404690  13.616949  12.970043  13.001899  13.107465
ENSMUSG00000003444   9.740093   9.965125  10.255192  10.080441  10.239468
ENSMUSG00000003452   8.584466   8.873925   8.484300   8.343031   8.470536
ENSMUSG00000003458  13.772460  14.094584  14.141134  14.222630  14.101553
ENSMUSG00000003464  15.710686  15.927966  15.985254  16.366943  16.360661
ENSMUSG00000003476   8.371126   8.516772   8.291178   8.464859   8.354330
ENSMUSG00000003477  18.304168  18.396668  19.052183  18.845412  18.852732
ENSMUSG00000003484   9.453696   9.6290

ENSMUSG00000004665  11.170962  11.240789   9.959686   9.827597   9.994350
ENSMUSG00000004667  12.751417  12.924121  12.736211  12.874044  12.943219
ENSMUSG00000004668   8.608162   8.319789   7.709728   7.674489   7.676749
ENSMUSG00000004677  13.328871  13.238663  13.185009  13.178867  13.234505
ENSMUSG00000004709   9.349786   9.126514   8.977295   8.557645   8.590269
ENSMUSG00000004730  13.680668  13.751370  13.336852  10.998317  10.946414
ENSMUSG00000004768  11.040183  11.191445  11.272033  11.917185  11.876144
ENSMUSG00000004771  13.880886  14.284985  13.589485  14.037025  13.992481
ENSMUSG00000004788  12.042490  12.098612  11.833204  12.143538  12.033375
ENSMUSG00000004789  15.965964  16.226042  16.663410  16.918268  16.885143
ENSMUSG00000004791   7.735140   8.159236   7.709728   7.674489   7.676749
ENSMUSG00000004815  13.258059  13.471359  13.378819  13.868038  13.922370
ENSMUSG00000004837  10.703217  10.596079  10.074619   9.742265   9.896804
ENSMUSG00000004843  13.014160  13.1168

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



   8.827011   7.709728   9.000450   8.184828
ENSMUSG00000008475  14.731843  14.684577  14.473201  14.470555  14.540609
ENSMUSG00000008496  11.840040  11.676103   9.725178   9.349988   9.289134
ENSMUSG00000008540  20.550998  20.616539  21.271368  20.974539  20.961371
ENSMUSG00000008590   7.735140   7.666953   7.709728   7.674489   7.676749
ENSMUSG00000008601   8.584466   8.882055   7.709728   8.699933   8.189166
ENSMUSG00000008658   7.735140   8.159236   8.291178   7.674489   7.676749
ENSMUSG00000008668  15.602572  15.563792  15.414595  15.624060  15.673515
ENSMUSG00000008682  17.719824  17.830926  17.505941  17.723910  17.713470
ENSMUSG00000008683  14.044904  14.016337  14.153598  14.428362  14.416144
ENSMUSG00000008690  14.873298  14.933539  15.751957  14.924404  15.102253
ENSMUSG00000008730  14.695623  14.688139  15.371229  15.432403  15.455364
ENSMUSG00000008763  12.660881  13.019436  13.868360  13.720939  13.838928
ENSMUSG00000008845  12.131949  12.426680  13.633808  10.854445  10.

ENSMUSG00000012126  10.523344  10.598329  10.002464   9.419990   9.610713
ENSMUSG00000012187   7.735140   8.516772   8.484300   9.087138   8.779086
ENSMUSG00000012282   7.735140   8.159236

In [14]:
%%R
training_indices <-
   caret::createDataPartition(
      tcdd_dose_detail_vec_tis_of_interest,
      times = 1,
      p = 1.0, # no data will be held out when set to "1.0"
      list = FALSE
   )
print(training_indices)

In [15]:
%%R
vst.count.mtx.train <-
   vst.count.mtx.tis_of_interest[, training_indices] #9/10ths of data
vst.count.mtx.test  <-
   vst.count.mtx.tis_of_interest[, -training_indices] #1/10th of data

print(vst.count.mtx.train)

  14.265496  13.737101  14.466572  14.543416
ENSMUSG00000002257   8.675309   8.556379   8.616090   8.905586   8.834083
ENSMUSG00000002279  13.145797  13.552159  13.542708  13.743744  13.625848
ENSMUSG00000002289  12.700055  12.532001  13.833389  12.456635  12.691994
ENSMUSG00000002297   9.698876   9.840043   9.540175   9.474437   9.349092
ENSMUSG00000002307  11.780019  11.792754  11.842684  11.957152  11.950948
ENSMUSG00000002308  10.435468  10.401556  10.094412  10.657760  10.341186
ENSMUSG00000002324   9.577450   9.348079   9.970151   9.026105   9.227664
ENSMUSG00000002325  13.541088  13.630173  13.558397  13.896160  14.023786
ENSMUSG00000002326  12.038827  12.062284  11.813995  11.876259  11.984988
ENSMUSG00000002346  15.680857  15.713684  15.567979  15.623532  15.652864
ENSMUSG00000002365  13.586443  13.628203  13.934015  13.895111  13.953438
ENSMUSG00000002379  14.104557  13.886007  13.945327  13.886698  13.745790
ENSMUSG00000002393  16.237011  16.208193  15.687835  16.032183  16.

ENSMUSG00000003411   8.675309   8.957830   8.567130   8.905586   8.756938
ENSMUSG00000003418   7.698795   8.252944   8.355980   7.697898   8.253319
ENSMUSG00000003421  12.662689  12.870980  12.914322  12.811247  12.697195
ENSMUSG00000003429  14.433870  14.458931  14.149579  13.814340  13.905967
ENSMUSG00000003435  15.097384  15.064868  14.495056  14.885617  14.851786
ENSMUSG00000003436   7.698795   7.697442   7.676469   7.697898   7.697563
ENSMUSG00000003437  13.366166  13.192639  13.361627  13.130409  12.849919
ENSMUSG00000003444  10.249861   9.883873  10.352836  10.151077  10.468803
ENSMUSG00000003452   8.441787   8.433572   7.676469   7.697898   8.437018
ENSMUSG00000003458  13.830104  13.782136  13.636601  14.075317  14.013167
ENSMUSG00000003464  15.394206  15.532551  15.533961  15.591723  15.527744
ENSMUSG00000003476   8.571542   8.902842   8.567130   7.697898   8.756938
ENSMUSG00000003477  18.805639  18.828895  19.463684  19.051491  19.018425
ENSMUSG00000003484   8.893427   9.3844

ENSMUSG00000004665  10.752781  10.508667  10.446733  10.670667  10.997473
ENSMUSG00000004667  13.211126  13.384324  13.038726  12.895322  13.014017
ENSMUSG00000004668   7.698795   8.252944   7.676469   7.697898   7.697563
ENSMUSG00000004677  13.608772  13.609427  13.205553  13.358415  13.280405
ENSMUSG00000004709   8.257141   8.668685   8.355980   8.254360   8.740366
ENSMUSG00000004730  12.542743  12.584998  10.857011  12.025721  11.990960
ENSMUSG00000004768  11.339014  11.059981  11.355616  11.274459  11.301250
ENSMUSG00000004771  14.363267  14.481430  14.419613  14.365265  14.282367
ENSMUSG00000004788  12.528320  12.705769  12.372989  12.394291  12.420969
ENSMUSG00000004789  16.802276  16.816413  16.721915  16.761923  16.828156
ENSMUSG00000004791   8.257141   8.252944   7.676469   7.697898   7.697563
ENSMUSG00000004815  13.842306  13.772940  13.937702  13.719646  13.647896
ENSMUSG00000004837   9.942946  10.207185  10.035666   9.934067  10.057085
ENSMUSG00000004843  12.776148  12.8754

ENSMUSG00000005716   7.698795   7.697442   7.676469   7.697898   7.697563
ENSMUSG00000005763  10.174277  10.018066   9.945332   9.927018  10.551710
ENSMUSG00000005779  15.698991  15.653067  15.734352  15.716785  15.780715
ENSMUSG00000005800   8.974996   9.272537   8.355980   7.697898   8.566083
ENSMUSG00000005803  15.987582  15.955569  16.524297  16.112706  16.213483
ENSMUSG00000005804  11.947661  11.961129  11.972878  12.061884  12.117996
ENSMUSG00000005813  13.778562  13.814211  13.571630  13.606377  13.429184
ENSMUSG00000005824   8.582847   8.666797   8.714772   8.670920   8.253319
ENSMUSG00000005836  10.649891  10.639810  10.739258  11.012649  11.017917
ENSMUSG00000005864   7.698795   7.697442   7.676469   7.697898   7.697563
ENSMUSG00000005871  13.080810  12.975206  13.454826  13.374290  13.533699
ENSMUSG00000005883   7.698795   8.252944   7.676469   8.254360   7.697563
ENSMUSG00000005886  14.058728  14.037742  14.207752  14.397618  14.435701
ENSMUSG00000005892   7.698795   7.6974

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



...

ENSMUSG00000005615  15.404459  15.453104  15.774515  15.719996
ENSMUSG00000005625  15.792760  15.788805  15.943314  15.930346
ENSMUSG00000005628   8.813320   8.954967   8.615173   8.418414
ENSMUSG00000005667   9.553900   9.659472   9.833376   9.474741
ENSMUSG00000005672  11.220354  11.083963  11.382062  11.392139
ENSMUSG00000005677  17.988365  18.004140  19.056319  19.060062
ENSMUSG00000005681  21.815856  21.820523  22.084897  22.094059
ENSMUSG00000005682  13.667886  13.768991  13.880468  13.820396
ENSMUSG00000005683  16.012642  15.917461  16.221890  16.289966
ENSMUSG00000005686   9.447194   9.210065   9.520389   9.624035
ENSMUSG00000005687  12.976569  12.851701  12.910042  13.002677
ENSMUSG00000005698  13.453612  13.645943  13.283011  13.259082
ENSMUSG00000005699   9.992184  10.068877  10.080120  10.401964
ENSMUSG00000005705   8.392941   8.372998   8.294722   8.645774
ENSMUSG00000005716   7.695696   7.695627   7.690665   7.692747
ENSMUSG00000005763  10.698746  10.550048  10.926624  10

ENSMUSG00000007480   7.695696   7.695627   7.690665   7.692747
ENSMUSG00000007564  14.560644  14.453895  14.740964  14.796057
ENSMUSG00000007570  10.661411  10.753207  10.739422  11.048481
ENSMUSG00000007613  12.758390  13.040127  13.429418  13.406932
ENSMUSG00000007617  11.114956  11.352260  11.185217  11.471872
ENSMUSG00000007646   8.557821   8.557517   8.622704   7.692747
ENSMUSG00000007653   7.695696   7.695627   7.690665   7.692747
ENSMUSG00000007655   9.596615   9.807354  10.007100   9.906296
ENSMUSG00000007656  13.869235  13.983841  14.453897  14.357264
ENSMUSG00000007659  13.144340  13.098329  12.311878  12.561649
ENSMUSG00000007670  13.785823  13.843806  13.654959  13.791226
ENSMUSG00000007682   7.695696   7.695627   7.690665   7.692747
ENSMUSG00000007739  14.932077  14.963358  14.865384  14.761792
ENSMUSG00000007812  13.426845  13.470135  14.541049  14.516986
ENSMUSG00000007815  15.541225  15.509116  15.349977  15.357216
ENSMUSG00000007827   9.990149  10.204364  10.566366  10

ENSMUSG00000011034   9.013808   8.954967   9.255653   9.141209
ENSMUSG00000011096  12.728123  12.764060  12.220601  12.157097
ENSMUSG00000011148  11.906766  11.722534  12.013925  11.974326
ENSMUSG00000011158  12.412686  12.570718  12.436067  12.470382
ENSMUSG00000011171   7.695696   7.695627   7.690665   7.692747
ENSMUSG00000011179  12.441741  12.513216  13.016827  13.212503
ENSMUSG00000011256   9.620064   9.562700   9.425025   9.702965
ENSMUSG00000011306  12.264247  12.131997  12.331362  12.325207
ENSMUSG00000011463   7.695696   7.695627   8.231971   7.692747
ENSMUSG00000011658  12.247556  12.377035  12.083674  12.274458
ENSMUSG00000011751   7.695696   7.695627   7.690665   7.692747
ENSMUSG00000011752  12.278027  12.266532  12.383650  12.465934
ENSMUSG00000011837  10.541598  10.767202  10.756477  10.775093
ENSMUSG00000011877  11.268829  11.294775  11.372370  11.256292
ENSMUSG00000011884   9.996245  10.132916  10.014162   9.875659
ENSMUSG00000011958  14.046267  13.896094  13.696211  13

ENSMUSG00000015627   7.695696   7.695627   8.531191   8.418414
ENSMUSG00000015647  10.440330  10.433290  10.057332  10.187017
ENSMUSG00000015653  11.101717  10.826860  10.386067  10.653346
ENSMUSG00000015656  17.400231  17.395830  17.492689  17.512647
ENSMUSG00000015665   7.695696   7.695627   7.690665   7.692747
ENSMUSG00000015668  11.969746  11.767522  12.170105  12.154594
ENSMUSG00000015671  14.675185  14.575630  14.837057  14.706371
ENSMUSG00000015672  12.839637  12.784729  12.764738  12.882340
ENSMUSG00000015697  13.750304  13.542783  13.645031  13.494727
ENSMUSG00000015709   7.695696   7.695627   7.690665   7.692747
ENSMUSG00000015714  17.448833  17.438091  17.680674  17.733747
ENSMUSG00000015733  15.105239  15.214561  14.992040  15.080054
ENSMUSG00000015747  11.024029  10.962873  10.759359  10.954224
ENSMUSG00000015748  11.632455  11.344841  11.042557  10.943143
ENSMUSG00000015750  14.840432  14.811113  14.813935  14.762184
ENSMUSG00000015755  15.343387  15.288563  13.933121  14

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [16]:
%%R
tcdd_dose_detail.vec.train <-
   tcdd_dose_detail_vec_tis_of_interest[training_indices]
tcdd_dose_detail.vec.test <-
   tcdd_dose_detail_vec_tis_of_interest[-training_indices]

# print(gtex_tissue_detail.vec.train)
print(length(unique(tcdd_dose_detail.vec.train)))

[1] 2


In [17]:
%%R
saveRDS(tcdd_dose_detail.vec.train,file=paste(OUT_DIR,"tcdd_dose_detail_vec_train1vs0_time_cross.Rds",sep=""))

In [18]:
%%R
cv_fold_indices <- caret::createFolds(tcdd_dose_detail.vec.train,
                                      k = N_FOLDS)
print(cv_fold_indices)

$Fold01
[1]  6 15 23 32 64 69 86 87 88

$Fold02
 [1]  3 35 43 48 49 68 73 82 93 94

$Fold03
[1]  1  2  7 14 20 21 52 61 70

$Fold04
[1] 25 37 38 44 53 58 76 79 85

$Fold05
[1]  8  9 19 26 45 57 78 89 91

$Fold06
 [1]  4 10 17 22 27 33 39 51 65 77

$Fold07
 [1]  5 41 71 74 75 80 83 84 90 92

$Fold08
[1] 16 18 28 31 42 46 55 66 67

$Fold09
 [1] 12 29 36 40 47 50 56 59 60 81

$Fold10
[1] 11 13 24 30 34 54 62 63 72



In [19]:
%%R
binary_tcdd_dose_annotations <- unique(tcdd_dose_detail.vec)
print(binary_tcdd_dose_annotations)

[1] 0 1


In [20]:
%%R
full_rxn_pca_results.nls <- list()
rxn_id_2_result_file_idx.nls <- list()

In [21]:
%%R
n_rxns <- length(rxns)
print(n_rxns)
result_idx <- 1
for(rxn_id_idx in seq(1:n_rxns)){
   rxn_id <- rxns[rxn_id_idx]
   rxn_pca <-
      prcomp(t(vst.count.mtx.train[rxn2ensembls.nls[[rxn_id]], ]), scale. = T)
   full_rxn_pca_results.nls[[rxn_id]] <- rxn_pca
   rxn_id_2_result_file_idx.nls[[rxn_id]] <- result_idx
   rxn_pca.nls[[rxn_id]] <-
      rxn_pca$x[, 1] # 1st principal component coordinate within this reaction-space for each sample
   if(mod(rxn_id_idx,100) == 0){
      print(paste("Processed ",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      flush.console()
   }
   if(mod(rxn_id_idx,1000) == 0){
      print(paste("Storing PCA objects containing reactions ",rxn_id_idx-1000,
                  "-",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      saveRDS(full_rxn_pca_results.nls,
              paste(OUT_DIR, "full_rxn_pca_results_nls",rxn_id_idx-1000,
                    "-",rxn_id_idx,"1vs0_time_cross.Rds", sep=""))
      full_rxn_pca_results.nls <- list()
      gc()
      result_idx <- result_idx + 1
   }
}

[1] 9825
[1] "Processed 100 of 9825 reactions (1%)..."
[1] "Processed 200 of 9825 reactions (2%)..."
[1] "Processed 300 of 9825 reactions (3.1%)..."
[1] "Processed 400 of 9825 reactions (4.1%)..."
[1] "Processed 500 of 9825 reactions (5.1%)..."
[1] "Processed 600 of 9825 reactions (6.1%)..."
[1] "Processed 700 of 9825 reactions (7.1%)..."
[1] "Processed 800 of 9825 reactions (8.2%)..."
[1] "Processed 900 of 9825 reactions (9.2%)..."
[1] "Processed 1000 of 9825 reactions (10.2%)..."
[1] "Storing PCA objects containing reactions 0-1000 of 9825 reactions (10.2%)..."
[1] "Processed 1100 of 9825 reactions (11.2%)..."
[1] "Processed 1200 of 9825 reactions (12.2%)..."
[1] "Processed 1300 of 9825 reactions (13.2%)..."
[1] "Processed 1400 of 9825 reactions (14.3%)..."
[1] "Processed 1500 of 9825 reactions (15.3%)..."
[1] "Processed 1600 of 9825 reactions (16.3%)..."
[1] "Processed 1700 of 9825 reactions (17.3%)..."
[1] "Processed 1800 of 9825 reactions (18.3%)..."
[1] "Processed 1900 of 9825 re

In [22]:
%%R
# store remaining PCA objects and removing from RAM
saveRDS(rxn_id_2_result_file_idx.nls,
        paste(OUT_DIR,"rxn_id_2_result_file_idx_nls1vs0_time_cross.Rds",sep=""))
saveRDS(full_rxn_pca_results.nls,
        paste(OUT_DIR, "full_rxn_pca_results_nls1vs0_time_cross.Rds", sep=""))
rm(full_rxn_pca_results.nls)
gc()

           used  (Mb) gc trigger  (Mb) max used  (Mb)
Ncells  6950713 371.3   13075702 698.4 11960543 638.8
Vcells 16060082 122.6   25877085 197.5 25877085 197.5


In [23]:
%%R
# compare informaction content of below files with pca plots or similar
saveRDS(rxn_pca.nls, paste(OUT_DIR, "rxn_pca_nls1vs0_time_cross.Rds", sep = ""))
saveRDS(vst.count.mtx.train,
        paste(OUT_DIR, "vst_count_mtx_train1vs0_time_cross.Rds", sep = ""))

In [24]:
%%R
for (cv_fold in names(cv_fold_indices)) {
  cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
}

In [25]:
%%R
# print(tissue_annotation)
# print(binary_tcdd_dose_annotations)
# print(paste("Processing tissue annotation:", tissue_annotation))
# print(length(binary_tcdd_dose_detail_vec.test.cv_test_list))
# print(sum(tcdd_dose_detail.vec.train.cv_test == tissue_annotation))
# print(length(rxns))

# binary_tcdd_dose_annotations <- c(0.00, 30.00, 0.01, 0.03, 0.10, 0.30, 1.00, 3.00, 10.00)

formatted_annotations <- format(binary_tcdd_dose_annotations, nsmall = 2)

formatted_annotations <- trimws(formatted_annotations)

binary_tcdd_dose_annotations <- formatted_annotations

print(binary_tcdd_dose_annotations)
for (annotation in binary_tcdd_dose_annotations) {
    print(annotation)
}

[1] "0.00" "1.00"
[1] "0.00"
[1] "1.00"


In [26]:
%%R
# main loop
for (rxn_id_idx in seq(1:length(rxns))) {
   rxn_id <- rxns[rxn_id_idx]
   ensembl_ids <- rxn2ensembls.nls[[rxn_id]]
   
   mean_misclass_rate <- list()
   sum_ari <- 0

   for (cv_fold in names(cv_fold_indices)) {
      cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
      
      vst.count.mtx.train.cv_train <-
         vst.count.mtx.train[, -cur_cv_fold_indices] # 4/5ths of training features
      vst.count.mtx.train.cv_test <-
         vst.count.mtx.train[, cur_cv_fold_indices] # 1/5th of training features
      
      tcdd_dose_detail.vec.train.cv_train <-
         tcdd_dose_detail.vec.train[-cur_cv_fold_indices] # 4/5ths of training labels
      tcdd_dose_detail.vec.train.cv_test <-
         tcdd_dose_detail.vec.train[cur_cv_fold_indices] # 1/5th of training labels
      
#        print(length(vst.count.mtx.train.cv_train))
#        print(length(gtex_tissue_detail.vec.train.cv_train))
       
      binary_tcdd_dose_detail_vec.test.cv_test_list <- list()
      for (tissue_annotation in binary_tcdd_dose_annotations) {
#          print(tcdd_dose_detail.vec.train.cv_test)
#          print("-------------")
#          print(tissue_annotation)
#          print(binary_tcdd_dose_detail_vec.test.cv_test_list)
         binary_tcdd_dose_detail_vec.test.cv_test_list[[as.character(tissue_annotation)]] <-
            (as.character(tcdd_dose_detail.vec.train.cv_test) == as.character(tissue_annotation))
      }
      
      cv_train.expr_mat <-
         t(vst.count.mtx.train.cv_train[ensembl_ids, ])
      cv_test.expr_mat <-
         t(vst.count.mtx.train.cv_test[ensembl_ids, ])
#        print(dim(cv_train.expr_mat))
#        print(length(gtex_tissue_detail.vec.train.cv_train))
      
      rxn_knn_calls <- class::knn(train = cv_train.expr_mat,
                                  test = cv_test.expr_mat,
                                  cl = tcdd_dose_detail.vec.train.cv_train)
      
      # calculate & store adjusted rand index
      cur_ari <- pdfCluster::adj.rand.index(rxn_knn_calls,
                                            tcdd_dose_detail.vec.train.cv_test)
      sum_ari <- cur_ari + sum_ari
      
      # for each tissue, calculate misclassification rate
      for (tissue_annotation in binary_tcdd_dose_annotations) {
         cur_rxn_knn_calls <- (rxn_knn_calls == tissue_annotation)
            
         # calculate misclassification rate (https://stat.ethz.ch/pipermail/r-help/2011-September/288885.html)
         tab <- table(cur_rxn_knn_calls,
                      binary_tcdd_dose_detail_vec.test.cv_test_list[[tissue_annotation]])
        # print(tab)
         cur_misclass_rate <- 1 - sum(diag(tab)) / sum(tab)
        # print(paste("Misclass rate = 1 - ",sum(diag(tab))," / ",sum(tab)," = ", cur_misclass_rate,"...",sep=""))
         sum_misclass_rate <- cur_misclass_rate
         if (!is.null(mean_misclass_rate[[tissue_annotation]])) {
           sum_misclass_rate <- sum_misclass_rate + mean_misclass_rate[[tissue_annotation]]
         }
         mean_misclass_rate[[tissue_annotation]] <- sum_misclass_rate
      }
   }
   for(tissue_annotation in binary_tcdd_dose_annotations){
      mean_misclass_rate[[tissue_annotation]] <- (mean_misclass_rate[[tissue_annotation]] / N_FOLDS)
   }
   mean_ari <- sum_ari / N_FOLDS
   ecount <- length(ensembl_ids)
   
   rxn_knn_misclass_rate.nls[[rxn_id]] <- mean_misclass_rate
   assign("mean_misclass_rate",NULL,envir = .GlobalEnv)
   
   rxn_knn_ari.nls[[rxn_id]] <- mean_ari
   rxn_knn_ecount.nls[[rxn_id]] <- ecount
   
   count <- count + 1
   if (mod(count, 10) == 0) {
      print(
         paste(
            "Last RXN_ID = ",
            rxn_id,
            ": Last ARI = ",
            mean_ari,
            ": Last ECOUNT = ",
            ecount,
            ": Last Lung MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Lung"]],
            ": Last Uterus MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Uterus"]],
            ". Now ",
            round(1.0 - count / length(rxns),3) * 100,
            "% remaining..."
         )
      )
      flush.console()
   }
}

[1] "Last RXN_ID =  R-MMU-749456 : Last ARI =  0.955555555555555 : Last ECOUNT =  178 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-9021601 : Last ARI =  0.873835125448029 : Last ECOUNT =  24 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-3108203 : Last ARI =  0.88578811369509 : Last ECOUNT =  15 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9838627 : Last ARI =  0.404359526531769 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-193679 : Last ARI =  0.288912176764289 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-194544 : Last ARI =  0.110103783068718 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.4 % remaining..."
[1] "Last 

[1] "Last RXN_ID =  R-MMU-8949580 : Last ARI =  0.904851330203443 : Last ECOUNT =  18 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-9692137 : Last ARI =  0.18750292644098 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-450580 : Last ARI =  0.835398691724256 : Last ECOUNT =  12 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-6791222 : Last ARI =  0.925925925925926 : Last ECOUNT =  61 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9696268 : Last ARI =  0.949295774647887 : Last ECOUNT =  41 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-1912394 : Last ARI =  0.827073552425665 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.4 % remaining..."
[1] "Las

[1] "Last RXN_ID =  R-MMU-3928625 : Last ARI =  0.31409574768687 : Last ECOUNT =  17 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-3928657 : Last ARI =  0.340525882386348 : Last ECOUNT =  10 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9034539 : Last ARI =  0.00792391873365822 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-983156 : Last ARI =  1 : Last ECOUNT =  242 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-174119 : Last ARI =  0.807168458781362 : Last ECOUNT =  18 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-174224 : Last ARI =  0.647123239143119 : Last ECOUNT =  18 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.3 % remaining..."
[1] "Last RXN_ID =  R-

[1] "Last RXN_ID =  R-MMU-8852134 : Last ARI =  0.617055577483254 : Last ECOUNT =  6 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-354124 : Last ARI =  0.955555555555555 : Last ECOUNT =  13 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-429415 : Last ARI =  0.866869951318675 : Last ECOUNT =  13 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-9714691 : Last ARI =  0.949295774647887 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-420980 : Last ARI =  0.0857956141433658 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-9013004 : Last ARI =  1 : Last ECOUNT =  16 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.1 % remaining..."
[1] "Last RXN_ID =  R-MMU

[1] "Last RXN_ID =  R-MMU-168162 : Last ARI =  0.28900017026213 : Last ECOUNT =  6 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-445079 : Last ARI =  0.426161743933091 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-8856808 : Last ARI =  0.719436250409702 : Last ECOUNT =  19 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-5607725 : Last ARI =  0.775221700573813 : Last ECOUNT =  14 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-174757 : Last ARI =  1 : Last ECOUNT =  10 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-187506 : Last ARI =  0.273984747998365 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.1 % remaining..."
[1] "Last RXN_ID =  R-NUL-96

...

[1] "Last RXN_ID =  R-MMU-9701485 : Last ARI =  0.0734791205593248 : Last ECOUNT =  5 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-2161187 : Last ARI =  0.0543823812108411 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-2168136 : Last ARI =  -0.00967618995576688 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-9623384 : Last ARI =  0.192214904179489 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-9007731 : Last ARI =  0.134055180612788 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-139919 : Last ARI =  0.140322532335277 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.1 % remaining..."
[1] "L

[1] "Last RXN_ID =  R-MMU-9758661 : Last ARI =  1 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-433089 : Last ARI =  0.00644614459797426 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-264679 : Last ARI =  0.106070659994639 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-9757578 : Last ARI =  0.106070659994639 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-374248 : Last ARI =  0.0959174929302376 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-3239019 : Last ARI =  0.27552564621358 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-8

[1] "Last RXN_ID =  R-MMU-9831009 : Last ARI =  -0.0357110441181238 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9833697 : Last ARI =  -0.0182469662120825 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-73569 : Last ARI =  -0.0612672856858903 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-5662620 : Last ARI =  0.10448832836614 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-6810452 : Last ARI =  0.498157420346001 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-2213240 : Last ARI =  0.114729664582946 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.1 % remaining..."
[1] "La

[1] "Last RXN_ID =  R-MMU-5578712 : Last ARI =  0.276945167738457 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-352052 : Last ARI =  0.300867478774456 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-1678921 : Last ARI =  0.251150195138949 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-9825053 : Last ARI =  0.364120526325734 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-1181347 : Last ARI =  0.0963905811617739 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-390886 : Last ARI =  0.26101337503406 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.1 % remaining..."
[1] "Last RXN_ID =

[1] "Last RXN_ID =  R-MMU-5340195 : Last ARI =  0.0367673634895583 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9708866 : Last ARI =  0.405587698971833 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-8959510 : Last ARI =  0.182968702894793 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-428585 : Last ARI =  0.00655693619890324 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-1483219 : Last ARI =  -0.0377816958176383 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-204662 : Last ARI =  0.276938996629435 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.1 % remaining..."
[1] "Last RXN

In [27]:
%%R
saveRDS(
   rxn_knn_misclass_rate.nls,
   paste(OUT_DIR, "toi_rxn_knn_misclass_rate_nls1vs0_time_cross.Rds", sep = "")
)
saveRDS(rxn_knn_ari.nls,
        paste(OUT_DIR, "toi_rxn_knn_ari_nls1vs0_time_cross.Rds", sep = ""))
saveRDS(rxn_knn_ecount.nls,
        paste(OUT_DIR, "toi_rxn_knn_ecount_nls1vs0_time_cross.Rds", sep = ""))

In [28]:
%%R
d <- data.frame(
   RXN_ID = names(rxn2ensembls.nls),
   MISCLASS = unlist(rxn_knn_misclass_rate.nls),
   ARI = unlist(rxn_knn_ari.nls),
   ECOUNT = unlist(rxn_knn_ecount.nls)
)
print(d)
saveRDS(d, paste(OUT_DIR, "toi_summary_df1vs0_time_cross.Rds", sep = ""))

                          RXN_ID MISCLASS           ARI ECOUNT
R-MMU-170666.0.00   R-MMU-170666        0  7.786865e-01     14
R-MMU-170666.1.00   R-MMU-170671        0  7.786865e-01     14
R-MMU-170671.0.00   R-MMU-170674        0  7.786865e-01     14
R-MMU-170671.1.00   R-MMU-170686        0  7.786865e-01     14
R-MMU-170674.0.00   R-MMU-380073        0  9.555556e-01    182
R-MMU-170674.1.00   R-MMU-392187        0  7.941891e-01     22
R-MMU-170686.0.00   R-MMU-392195        0  7.941891e-01     22
R-MMU-170686.1.00   R-MMU-392202        0  7.941891e-01     22
R-MMU-380073.0.00   R-MMU-749454        0  9.555556e-01    178
R-MMU-380073.1.00   R-MMU-749456        0  9.555556e-01    178
R-MMU-392187.0.00   R-MMU-751001        0  9.157325e-01     21
R-MMU-392187.1.00  R-MMU-8964229        0  3.974587e-01      5
R-MMU-392195.0.00  R-MMU-8964242        0  3.974587e-01      5
R-MMU-392195.1.00  R-MMU-8964329        0  3.974587e-01      5
R-MMU-392202.0.00  R-MMU-8982012        0  5.495605e-01

R-MMU-205112.1.00  R-MMU-5654397        0  3.251954e-01     16
R-MMU-205117.0.00  R-MMU-5654399        0  3.251954e-01     16
R-MMU-205117.1.00  R-MMU-5654402        0  9.111111e-01     20
R-MMU-209532.0.00  R-MMU-5654404        0  6.078699e-01     16
R-MMU-209532.1.00  R-MMU-5654406        0  7.471976e-01     18
R-MMU-209566.0.00  R-MMU-5654407        0  6.078699e-01     16
R-MMU-209566.1.00  R-MMU-5654408        0  5.576839e-01     12
R-MMU-9012761.0.00 R-MMU-5654409        0  5.576839e-01     12
R-MMU-9012761.1.00 R-MMU-5654413        0  9.601770e-01     17
R-MMU-3247837.0.00 R-MMU-5654416        0  7.947854e-01     15
R-MMU-3247837.1.00 R-MMU-5654418        0  9.157325e-01     14
R-MMU-3247840.0.00 R-MMU-5654422        0  9.157325e-01     14
R-MMU-3247840.1.00 R-MMU-5654423        0  8.707325e-01     16
R-MMU-3247843.0.00 R-MMU-5654425        0  8.712881e-01     14
R-MMU-3247843.1.00 R-MMU-5654426        0  1.000000e+00     18
R-MMU-3247844.0.00 R-MMU-5654428        0  8.712881e-01

R-MMU-5654397.1.00 R-MMU-9753126        0  2.046580e-01      5
R-MMU-5654399.0.00  R-MMU-514604        0  1.394564e-01      2
R-MMU-5654399.1.00  R-MMU-975389        0  1.405957e-01      4
R-MMU-5654402.0.00 R-MMU-1169394        0  7.198002e-01      5
R-MMU-5654402.1.00 R-MMU-1169398        0  5.642348e-01      5
R-MMU-5654404.0.00 R-MMU-1169402        0  5.413437e-01      6
R-MMU-5654404.1.00 R-MMU-1169403        0  2.788252e-01      4
R-MMU-5654406.0.00 R-MMU-1169405        0  3.935854e-01      5
R-MMU-5654406.1.00 R-MMU-1169406        0  9.048513e-01     12
R-MMU-5654407.0.00 R-MMU-1678842        0  9.492958e-01     13
R-MMU-5654407.1.00 R-MMU-1678843        0  6.267556e-01      5
R-MMU-5654408.0.00 R-MMU-5653754        0  8.307773e-01     21
R-MMU-5654408.1.00 R-MMU-5653756        0  7.638807e-01     19
R-MMU-5654409.0.00 R-MMU-9833973        0  5.153258e-01      5
R-MMU-5654409.1.00  R-MMU-426240        0  5.691626e-01     10
R-MMU-5654413.0.00  R-MMU-199050        0  6.518388e-01

R-MMU-5654664.1.00  R-MMU-389158        0  3.675971e-01      9
R-MMU-5654667.0.00  R-MMU-389348        0  1.244140e-01      8
R-MMU-5654667.1.00  R-MMU-389350        0  2.152070e-01      8
R-MMU-5654669.0.00  R-MMU-389352        0  1.050019e-01      7
R-MMU-5654669.1.00  R-MMU-389354        0  1.050019e-01      7
R-MMU-5654672.0.00  R-MMU-389381        0  4.273707e-02      6
R-MMU-5654672.1.00  R-MMU-389758        0  6.569003e-01     22
R-MMU-5654673.0.00  R-MMU-389759        0  4.396940e-01      7
R-MMU-5654673.1.00  R-MMU-389762        0  3.284438e-01      5
R-MMU-5654677.0.00  R-MMU-434836        0  7.664562e-02      3
R-MMU-5654677.1.00  R-MMU-452100        0  2.860749e-01      6
R-MMU-5654679.0.00 R-MMU-8852200        0  4.373857e-01     17
R-MMU-5654679.1.00 R-MMU-8855381        0  4.978158e-01     18
R-MMU-5654684.0.00 R-MMU-8857925        0  9.259259e-01     15
R-MMU-5654684.1.00 R-MMU-9706312        0  1.018326e-01      2
R-MMU-5654690.0.00 R-MMU-8849348        0  7.061421e-01

R-MMU-9753126.1.00  R-MMU-450580        0  8.353987e-01     12
R-MMU-514604.0.00    R-MMU-72103        0  1.000000e+00     43
R-MMU-514604.1.00  R-MMU-9770119        0  1.000000e+00     69
R-MMU-975389.0.00  R-MMU-9770141        0  1.000000e+00    123
R-MMU-975389.1.00  R-MMU-9770142        0  1.000000e+00    132
R-MMU-1169394.0.00 R-MMU-9770145        0  1.000000e+00    145
R-MMU-1169394.1.00 R-MMU-9770236        0  1.000000e+00    119
R-MMU-1169398.0.00 R-MMU-6798748        0  1.000000e+00    106
R-MMU-1169398.1.00 R-MMU-6800434        0  9.492958e-01    134
R-MMU-1169402.0.00 R-MMU-6791218        0  1.000000e+00     68
R-MMU-1169402.1.00 R-MMU-6791222        0  9.259259e-01     61
R-MMU-1169403.0.00 R-MMU-1605595        0  9.071685e-01      3
R-MMU-1169403.1.00 R-MMU-1605624        0  1.199369e-01      6
R-MMU-1169405.0.00 R-MMU-1605717        0  3.294576e-03      1
R-MMU-1169405.1.00 R-MMU-6798751        0  1.000000e+00    105
R-MMU-1169406.0.00 R-MMU-9840795        0  1.098305e-01

...

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)




R-MMU-9816449.1.00  R-MMU-418172        0  6.665747e-01      2
R-MMU-8849857.0.00 R-MMU-9708866        0  4.055877e-01      1
R-MMU-8849857.1.00 R-MMU-9006144        0  1.868158e-01      1
R-MMU-1461971.0.00 R-MMU-5336430        0  4.234847e-02      2
R-MMU-1461971.1.00 R-MMU-5687126        0  3.713734e-02      1
R-MMU-1461982.0.00 R-MMU-9624527        0  3.713734e-02      1
R-MMU-1461982.1.00 R-MMU-9699581        0  3.713734e-02      1
R-MMU-1461995.0.00 R-MMU-5619439        0  3.310719e-02      1
R-MMU-1461995.1.00  R-MMU-417896        0  6.998044e-02      1
R-MMU-1462003.0.00 R-MMU-9634937        0  4.104518e-02      1
R-MMU-1462003.1.00  R-MMU-381608        0 -1.332970e-02      1
R-MMU-1462005.0.00 R-MMU-8959510        0  1.829687e-01      1
R-MMU-1462005.1.00 R-MMU-9034714        0  1.013296e-01      2
R-MMU-1462014.0.00 R-MMU-9615249        0  5.708679e-02      1
R-MMU-1462014.1.00 R-MMU-3296326        0  6.606581e-02      1
R-MMU-1462039.0.00 R-MMU-5205798        0  2.288973e-0

R-MMU-6786421.1.00 R-NUL-4649029        0  3.326587e-02      1
R-MMU-109341.0.00  R-MMU-1482861        0  1.589963e-02      1
R-MMU-109341.1.00  R-MMU-1482867        0  1.589963e-02      1
R-MMU-77338.0.00   R-MMU-9663768        0 -3.871603e-02      1
R-MMU-77338.1.00   R-MMU-9749977        0  6.628637e-01      2
R-MMU-77345.0.00    R-MMU-266204        0  3.957645e-01      2
R-MMU-77345.1.00    R-MMU-419334        0 -6.911437e-03      1
R-MMU-1237160.0.00 R-MMU-5638333        0  2.612702e-01     14
R-MMU-1237160.1.00 R-MMU-5649800        0  2.612702e-01     14
R-MMU-6810376.0.00 R-MMU-5649802        0  2.612702e-01     14
R-MMU-6810376.1.00 R-MMU-9696274        0  4.148842e-02      1
R-MMU-5674385.0.00  R-MMU-109380        0  1.044883e-01      1
R-MMU-5674385.1.00  R-MMU-109387        0  1.044883e-01      1
R-MMU-9610166.0.00 R-NUL-2974720        0  1.441353e-01      1
R-MMU-9610166.1.00 R-MMU-6811479        0  1.710525e-01      3
R-MMU-2408505.0.00 R-MMU-6811508        0  1.710525e-01

R-MMU-176588.1.00  R-MMU-9606621        0  4.056589e-01      2
R-MMU-176604.0.00  R-MMU-9606623        0  4.056589e-01      2
R-MMU-176604.1.00  R-MMU-1482973        0  2.671237e-01      1
R-MMU-888572.0.00  R-MMU-5205867        0  7.549608e-02     20
R-MMU-888572.1.00  R-MMU-1855185        0  1.710400e-01      1
R-MMU-9007901.0.00 R-MMU-1855206        0  1.710400e-01      1
R-MMU-9007901.1.00 R-MMU-1855228        0  1.710400e-01      1
R-MMU-199216.0.00  R-MMU-1855233        0  1.710400e-01      1
R-MMU-199216.1.00  R-MMU-1449687        0  5.396418e-01      1
R-MMU-3296304.0.00 R-MMU-9757686        0  5.396418e-01      1
R-MMU-3296304.1.00 R-MMU-9757688        0  5.396418e-01      1
R-MMU-391935.0.00  R-MMU-6814096        0  8.887597e-02      2
R-MMU-391935.1.00  R-MMU-5602295        0  1.052915e-01      1
R-MMU-8956458.0.00 R-MMU-9832937        0  1.348259e-01      2
R-MMU-8956458.1.00 R-MMU-9832947        0  1.348259e-01      2
R-MMU-977389.0.00  R-MMU-5649764        0  2.028404e-01

R-MMU-6799981.1.00  R-MMU-351222        0  7.457368e-02      1
R-MMU-174916.0.00  R-MMU-6786245        0  2.339529e-02      1
R-MMU-174916.1.00  R-MMU-6808464        0  1.434894e-01      1
R-MMU-8941701.0.00 R-MMU-9724685        0  1.108027e-01     59
R-MMU-8941701.1.00 R-MMU-5619422        0  7.958873e-02      1
R-MMU-904864.0.00   R-MMU-446195        0  1.009746e-01      1
R-MMU-904864.1.00  R-MMU-9018868        0 -4.945484e-02      1
R-MMU-429663.0.00  R-MMU-9018895        0 -4.945484e-02      1
R-MMU-429663.1.00  R-MMU-9020271        0 -4.945484e-02      1
R-MMU-8954327.0.00 R-MMU-9020273        0 -4.945484e-02      1
R-MMU-8954327.1.00  R-MMU-350869        0  3.261708e-01      1
R-MMU-159179.0.00  R-MMU-5696004        0  7.140467e-03      1
R-MMU-159179.1.00  R-MMU-9670578        0  9.100963e-02      3
R-MMU-159194.0.00  R-MMU-8955010        0  1.384162e-01      1
R-MMU-159194.1.00    R-MMU-71825        0  3.411842e-01      1
R-MMU-9756134.0.00 R-MMU-5696146        0  8.660091e-02

In [29]:
%%R
pid <- read.table(paste(OUT_DIR,"tcdd_project_id1vs0_time_cross.txt",sep=""),header=FALSE)
sid <- read.table(paste(OUT_DIR,"tcdd_sample_id1vs0_time_cross.txt",sep=""), header=FALSE)
sex <- read.table(paste(OUT_DIR, "tcdd_gender1vs0_time_cross.txt", sep=""), header=FALSE)
print(sex)

       V1
1    male
2    male
3    male
4    male
5    male
6    male
7    male
8    male
9    male
10   male
11   male
12   male
13   male
14   male
15   male
16   male
17   male
18   male
19   male
20   male
21   male
22   male
23   male
24   male
25   male
26   male
27   male
28   male
29   male
30   male
31   male
32   male
33   male
34   male
35   male
36   male
37   male
38   male
39   male
40   male
41   male
42   male
43   male
44   male
45   male
46   male
47   male
48   male
49 female
50 female
51 female
52 female
53 female
54 female
55 female
56 female
57 female
58 female
59 female
60 female
61 female
62 female
63 female
64 female
65 female
66 female
67 female
68 female
69 female
70 female
71 female
72 female
73 female
74 female
75 female
76 female
77 female
78 female
79 female
80 female
81 female
82 female
83   male
84   male
85   male
86   male
87   male
88   male
89   male
90   male
91   male
92   male
93   male
94   male


In [30]:
%%R
library(htmlwidgets)
min_misclass_pca <-
   prcomp(t(vst.count.mtx.train), scale. = T)
pca.d <- data.frame(
   PC1 = min_misclass_pca$x[, 1],
   PC2 = min_misclass_pca$x[, 2],
   PC3 = min_misclass_pca$x[, 3],
   Section = tcdd_dose_detail.vec.train,
   Project_id = pid$V1,
   Sample_id = sid$V1
)

ggplot(pca.d, aes(x = PC1, y = PC2, colour = Section)) +
   geom_point(size = 3) +  # 绘制点，指定点的大小
   geom_text(aes(label = paste(Project_id, Sample_id)), vjust = -1, hjust = 1, size = 2) +  # 添加标签
   scale_colour_manual(values = c("0" = "red", "1" = "green")) +  # 手动指定颜色
   theme_bw()

p <- plot_ly(
   data = pca.d,
   x = ~PC1,
   y = ~PC2,
   z = ~PC3,
   type = "scatter3d",
   mode = "markers",
   marker = list(
     color = as.factor(pca.d$Section),  # 将 Section 转换为因子
     colors = c("red", "green"),  # 定义颜色
     size = 5
   ),
   text = ~paste("Project ID:", Project_id, "Sample ID:", Sample_id)  # 在悬停文本中显示 Project ID
)
saveWidget(p, "plotly_chart1vs0_time_cross.html", selfcontained = TRUE)